In [200]:
import cv2
import numpy as np
np.set_printoptions(threshold=np.nan)

### 이미지를 흑백으로 변환

In [201]:
img = cv2.imread('../image/out_of_focus0015.jpg', cv2.IMREAD_GRAYSCALE)
img = cv2.normalize(img.astype('float64'), None, 0.0, 1.0, cv2.NORM_MINMAX)

In [202]:
patchsize = 11

### localBlurScore 부분

In [203]:
im_height, im_width = img.shape
offset = int((patchsize -1)/2)
x_start = offset+1; x_end = im_width-offset;
y_start = offset+1; y_end = im_height-offset;
datasize = (x_end-x_start+1)*(y_end-y_start+1)

### LocalKurtosis.m 부분

In [204]:
dx = np.c_[np.diff(img),-img[:,-1]]
dy = np.r_['0,2',np.diff(img,axis=0),-img[-1,:]]

In [207]:
np.square(q / np.sum(q,1))

array([[  2.26757370e-03,   1.23114805e-03,   1.04058273e-03,
          9.61480680e-04,   9.18273646e-04,   8.91067053e-04],
       [  1.11111111e-01,   1.96983687e-02,   9.36524454e-03,
          6.00925425e-03,   4.44444444e-03,   3.56426821e-03],
       [  3.83219955e-01,   6.03262542e-02,   2.60145682e-02,
          1.53836909e-02,   1.06152433e-02,   8.01960348e-03],
       [  8.18594104e-01,   1.23114805e-01,   5.09885536e-02,
          2.90847906e-02,   1.94306703e-02,   1.42570728e-02],
       [  1.41723356e+00,   2.08064020e-01,   8.42872008e-02,
          4.71125533e-02,   3.08907254e-02,   2.22766763e-02],
       [  2.17913832e+00,   3.15173900e-01,   1.25910510e-01,
          6.94669791e-02,   4.49954086e-02,   3.20784139e-02]])

In [208]:
dx_col = im2col(dx,[patchsize,patchsize])
dx_col = dx_col / np.sum(dx_col,1,keepdims=True)

In [209]:
dy_col = im2col(dy,[patchsize,patchsize])
dy_col = dy_col / np.sum(dy_col,1,keepdims=True)

In [210]:
normXsquare = np.square(dx_col - np.mean(dx_col))
normYsquare = np.square(dy_col - np.mean(dy_col))

In [213]:
qx = np.mean(np.square(normXsquare),axis=0,keepdims=True) / np.square(np.mean(normXsquare,axis=0,keepdims=True))
qy = np.mean(np.square(normYsquare),axis=0,keepdims=True) / np.square(np.mean(normYsquare,axis=0,keepdims=True))

In [215]:
qx = np.reshape(qx, [im_height-patchsize+1, im_width-patchsize+1])
qy = np.reshape(qy, [im_height-patchsize+1, im_width-patchsize+1])

In [216]:
qx = np.log(np.pad(qx,offset,mode='edge'))
qy = np.log(np.pad(qy,offset,mode='edge'))

In [217]:
qx[np.isnan(qx)] = np.min(np.min(qx[~np.isnan(qx)]))
qy[np.isnan(qy)] = np.min(np.min(qy[~np.isnan(qy)]))

In [218]:
q = np.minimum(qx,qy)

In [220]:
q

array([[  2.18036776e+00,   2.18036776e+00,   2.18036776e+00,
          2.18036776e+00,   2.18036776e+00,   2.18036776e+00,
          2.04168878e+00,   1.83703561e+00,   1.79302961e+00,
          1.79791854e+00,   1.73103293e+00,   1.58983456e+00,
          1.57796619e+00,   1.43849940e+00,   1.50532945e+00,
          1.50920517e+00,   1.58613241e+00,   1.80462588e+00,
          1.94211578e+00,   2.18559881e+00,   2.30988537e+00,
          2.40147505e+00,   2.38969142e+00,   2.38133254e+00,
          2.37121888e+00,   2.35751339e+00,   2.34679173e+00,
          2.19646566e+00,   2.23843670e+00,   2.29483893e+00,
          2.27358151e+00,   2.27072207e+00,   2.31128816e+00,
          2.32622167e+00,   2.37901471e+00,   2.35209098e+00,
          2.31479859e+00,   2.38557786e+00,   2.09488085e+00,
          2.02626164e+00,   1.90824624e+00,   1.80846089e+00,
          1.79140745e+00,   1.97915205e+00,   1.98299887e+00,
          2.05428349e+00,   2.09561594e+00,   2.16655410e+00,
        

In [7]:
def im2col(A, BSZ):
    # Parameters
    A = np.transpose(A)
    m,n = A.shape
    s0, s1 = A.strides    
    nrows = m-BSZ[0]+1
    ncols = n-BSZ[1]+1
    shp = BSZ[0],BSZ[1],nrows,ncols
    strd = s0,s1,s0,s1

    out_view = np.lib.stride_tricks.as_strided(A, shape=shp, strides=strd)
    return out_view.reshape(BSZ[0]*BSZ[1],-1)[:,::1]
